In [86]:
import requests
import time
import boto3
import pandas as pd
import io
import json
from typing import List, Dict, Any

all_Cards = []



In [ ]:
last = False

while last == False:
    try:
        response = requests.get(url)

        list_rels = response.headers.get('Link').split(",")
        list_rels_comp = [item.split(";") for item in list_rels]

        dict_rels = {rel[1].replace("rel=", "").replace('"', '').replace(" ","") : rel[0].replace("<","").replace(">","").replace(" ","") for rel in list_rels_comp}
        
        all_Cards.extend(response.json()["cards"])
        
        if "next" in dict_rels:
            url = dict_rels["next"]
            time.sleep(1)
        else:
            last = True
    except requests.exceptions.HTTPError as e:
        print(f"Error HTTP ({e.response.status_code}). Reintentando en 5s...")
        time.sleep(5)
    except requests.exceptions.RequestException as e:
        print(f"Error de conexión: {e}. Reintentando en 5s...")
        time.sleep(5)
    except Exception as error:
        print(f"Ha ocurrido otro error: {error}")

### DESCARGA DESDE BULK

In [87]:
all_Cards = requests.get("https://data.scryfall.io/default-cards/default-cards-20251023090836.json").json()

In [88]:
def get_spanish_value(card_data, key_to_extract):
    foreign_names = card_data.get("foreignNames")
    if foreign_names:
        for item in foreign_names:
            if item.get("language") == "Spanish":
                return item.get(key_to_extract, "")
    return ""

def get_formats(legalities: Dict[str, str]) -> List[str]:
    if isinstance(legalities, dict):
        return [
            formato
            for formato, estatus in legalities.items()
            if estatus == "legal"
        ]
    return []


In [ ]:
all_Cards
all_cards_cleaned = [{
        "nombre": card.get("name"),
        "texto": card.get("oracle_text"),
        "coste": card.get("mana_cost", ""),
        "identidad_Color": card.get("color_identity"),
        "tipo": card.get("type_line"),
        "set": card.get("set_name"),
        "rareza": card.get("rarity"),

        "fuerza": card.get("power", None), 
        "resistencia": card.get("toughness", None),
        
        "cmc": card.get("cmc", None),
        "formatos_legales": get_formats((card.get("legalities", {}))),
        "reserved_list": card.get("reserved"),
        "game_changer": card.get("game_changer")
        "precio": card["prices"]["eur"]
    } for card in all_Cards]

df_cards = pd.DataFrame(all_cards_cleaned)


In [90]:
df_cards

nombre  \
0                    Forest   
1               Fury Sliver   
2             Kor Outfitter   
3                    Spirit   
4             Siren Lookout   
...                     ...   
110242       Celestine Reef   
110243         Horned Troll   
110244  Faerie Bladecrafter   
110245  Exultant Skymarcher   
110246         Disintegrate   

                                                    texto      coste  \
0                                         ({T}: Add {G}.)              
1                All Sliver creatures have double strike.     {5}{R}   
2       When this creature enters, you may attach targ...     {W}{W}   
3                                                  Flying              
4       Flying\nWhen this creature enters, it explores...     {2}{U}   
...                                                   ...        ...   
110242  Creatures without flying or islandwalk can't a...              
110243                     {G}: Regenerate this creature.     {2}{G}   
110244  Flying\nWhenever one or more Faeries you contr...     {2}{B}   
110245                                             Flying  {1}{W}{W}   
110246  Disintegrate deals X damage to any target. If ...     {X}{R}   

       identidad_Color                        tipo  \
0                  [G]         Basic Land — Forest   
1                  [R]           Creature — Sliver   
2                  [W]      Creature — Kor Soldier   
3                  [W]     Token Creature — Spirit   
4                  [U]     Creature — Siren Pirate   
...                ...                         ...   
110242              []              Plane — Luvion   
110243             [G]            Creature — Troll   
110244             [B]     Creature — Faerie Rogue   
110245             [W]  Creature — Vampire Soldier   
110246             [R]                     Sorcery   

                                set fuerza resistencia  cmc  \
0                       Bloomburrow   None        None  0.0   
1                       Time Spiral      3           3  6.0   
2                          Zendikar      2           2  2.0   
3        Modern Masters 2015 Tokens      1           1  0.0   
4                            Ixalan      1           2  3.0   
...                             ...    ...         ...  ...   
110242                   DCI Promos   None        None  0.0   
110243               Eighth Edition      2           2  3.0   
110244  Wilds of Eldraine Commander      2           2  3.0   
110245             Rivals of Ixalan      2           3  3.0   
110246     30th Anniversary Edition   None        None  1.0   

                                         formatos_legales precio  
0       [standard, future, historic, timeless, gladiat...   0.24  
1       [modern, legacy, vintage, commander, oathbreak...   0.17  
2       [modern, legacy, pauper, vintage, penny, comma...   0.10  
3                                                      []   None  
4       [historic, timeless, gladiator, pioneer, moder...   0.12  
...                                                   ...    ...  
110242                                                 []   0.54  
110243  [modern, legacy, pauper, vintage, penny, comma...   0.09  
110244    [legacy, vintage, commander, oathbreaker, duel]   1.10  
110245  [historic, timeless, gladiator, pioneer, moder...   0.05  
110246  [modern, legacy, pauper, vintage, commander, o...   None  

[110247 rows x 11 columns]

In [97]:
df_cards[df_cards["nombre"]=="The Soul Stone"]

nombre                                              texto  \
11147   The Soul Stone  Indestructible\n{T}: Add {B}.\n{6}{B}, {T}, Ex...   
19134   The Soul Stone  Indestructible\n{T}: Add {B}.\n{6}{B}, {T}, Ex...   
29680   The Soul Stone  Indestructible\n{T}: Add {B}.\n{6}{B}, {T}, Ex...   
71330   The Soul Stone  Indestructible\n{T}: Add {B}.\n{6}{B}, {T}, Ex...   
107626  The Soul Stone  Indestructible\n{T}: Add {B}.\n{6}{B}, {T}, Ex...   

         coste identidad_Color                                 tipo  \
11147   {1}{B}             [B]  Legendary Artifact — Infinity Stone   
19134   {1}{B}             [B]  Legendary Artifact — Infinity Stone   
29680   {1}{B}             [B]  Legendary Artifact — Infinity Stone   
71330   {1}{B}             [B]  Legendary Artifact — Infinity Stone   
107626  {1}{B}             [B]  Legendary Artifact — Infinity Stone   

                               set fuerza resistencia  cmc  \
11147          Marvel's Spider-Man   None        None  2.0   
19134          Marvel's Spider-Man   None        None  2.0   
29680   Marvel's Spider-Man Promos   None        None  2.0   
71330        Through the Omenpaths   None        None  2.0   
107626         Marvel's Spider-Man   None        None  2.0   

                                         formatos_legales precio  
11147   [standard, future, historic, timeless, gladiat...  47.70  
19134   [standard, future, historic, timeless, gladiat...   None  
29680   [standard, future, historic, timeless, gladiat...   None  
71330   [standard, future, historic, timeless, gladiat...   None  
107626  [standard, future, historic, timeless, gladiat...   None

In [95]:
all_Cards

[{'object': 'card',
  'id': '0000419b-0bba-4488-8f7a-6194544ce91e',
  'oracle_id': 'b34bb2dc-c1af-4d77-b0b3-a0fb342a5fc6',
  'multiverse_ids': [668564],
  'mtgo_id': 129825,
  'arena_id': 91829,
  'tcgplayer_id': 558404,
  'cardmarket_id': 777725,
  'name': 'Forest',
  'lang': 'en',
  'released_at': '2024-08-02',
  'uri': 'https://api.scryfall.com/cards/0000419b-0bba-4488-8f7a-6194544ce91e',
  'scryfall_uri': 'https://scryfall.com/card/blb/280/forest?utm_source=api',
  'layout': 'normal',
  'highres_image': True,
  'image_status': 'highres_scan',
  'image_uris': {'small': 'https://cards.scryfall.io/small/front/0/0/0000419b-0bba-4488-8f7a-6194544ce91e.jpg?1721427487',
   'normal': 'https://cards.scryfall.io/normal/front/0/0/0000419b-0bba-4488-8f7a-6194544ce91e.jpg?1721427487',
   'large': 'https://cards.scryfall.io/large/front/0/0/0000419b-0bba-4488-8f7a-6194544ce91e.jpg?1721427487',
   'png': 'https://cards.scryfall.io/png/front/0/0/0000419b-0bba-4488-8f7a-6194544ce91e.png?1721427487',